# Lariat Displays and Movies with ParaView

Adam Lyon / Fermilab SCD / September 2015

!! Not complete !!

The plan is to demonstrate use of ParaView to make some simple, but effective, event displays of Liquid Argon neutrino data with not too much effort. See Jim Kowalkowski's notes at https://github.com/jbkowalkowski/AnalysisWork/wiki/Geant4-visualization-and-LArSoft for more information.

Jim has code (see link above) that can write out event data from Lariat from one event (for now). He generates comma-separated-value files (`.csv`) with this data. I have a script `convertCSV.py` that converts the csv file into VTK PolyData and writes that out to a `.vtp` file that ParaView can load directly. Each row of the csv must contain a 3-D position $(x,y,z)$ and then additional columns of metadata that can be integers, floats, or strings. The script will automatically create vectors out of neighboring columns whose titles end in `x`, `y`, `z`. For example, three columns in a row named `px, py, pz` will be turned into a vector called `p`. Other column metadata are turned into scalars. The script associates the metadata with each point. Each point is also a `VTK_VERTEX` cell, but the cell has no metadata (the ParaView `Point Data To Cell Data` filter can copy the point data to the cells if they are needed). 

## Hit and track information

Let's first look at some basic hit & track information. Jim has a file called `output_po.csv` containing hits and metadata.

In [1]:
!head data20150919/output_po.csv

eid/I,type/S,id/I,index/I,x/F,y/F,z/F,dirx/F,diry/F,dirz/F,p/F
1,pmtrack,0,0,29.4108,-1.02638,50.6487,0.10971,0.035345,-0.993335,0
1,pmtrack,0,1,29.4585,-1.01102,50.217,0.10971,0.035345,-0.993335,0
1,pmtrack,0,2,29.5111,-0.994092,49.7413,0.10971,0.035345,-0.993335,0
1,pmtrack,0,3,29.541,-0.984435,49.4699,0.10971,0.035345,-0.993335,0
1,pmtrack,0,4,29.5606,-0.978127,49.2927,0.10971,0.035345,-0.993335,0
1,pmtrack,0,5,29.5959,-0.966758,48.9731,0.10971,0.035345,-0.993335,0
1,pmtrack,0,6,29.611,-0.961909,48.8369,0.10971,0.035345,-0.993335,0
1,pmtrack,0,7,29.6475,-0.95012,48.5055,0.10971,0.035345,-0.993335,0
1,pmtrack,0,8,29.6612,-0.945724,48.382,0.10971,0.035345,-0.993335,0


The first line is the header with the column name followed by the type (`I` is integer, `F` is float, `S` is string). The types are needed by my `convertCSV.py` script. 

The data contain rows of hits. Each hit row has:
* `eid` The event ID (always 1 since we only have one event)
* `type` The track type (`pmtrack`, `costrack`, `cctrack`) representing the tracking algorithm that produced the track. 
* `id` The ID of the track
* `index` The index of the hit on the track (starts at 0 for new track)
* `x,y,z` The position of the hit
* `dirx, diry, dirz` The track direction at the hit
* `p` Not sure what this is, but it's always zero

We can convert this to the vtp file,

In [2]:
!pvpython convertCSV.py data20150919/output_po.csv

Read File
[('eid', '<i8'), ('type', 'S20'), ('id', '<i8'), ('index', '<i8'), ('x', '<f8'), ('y', '<f8'), ('z', '<f8'), ('dirx', '<f8'), ('diry', '<f8'), ('dirz', '<f8'), ('p', '<f8')]
Assemble polydata
Making array eid
Making array (string) type
Making array id
Making array index
Making array dirx diry dirz
Making array p
Writing output_po.vtp


Let's display this data in ParaView. General instructions will be given for creating the visualizations in this notebook. For each there is a ParaView state file that you can load yourself in ParaView to see the visualization and manipulate it further. For the notebook, we'll run `pvpython` to generate the images/movies for display. We will use ParaView v4.4 (and you should too).

To get some basic information, load the `output_po.vtp` file in ParaView (be sure to press the `Apply` button from the properties panel to execute). Load in all of the arrays from the "Cell/Point Array Status" box in the properties panel. 

Coloring the hits by track algorithm would be useful. Choose `type` from the color drop-down list (with `Surface` selected in the list near it) and open the Color Map Editor. Be sure `Interpret Values as Categories` is checked. In the `Annotations` box, click on the `Add Active values from selected source` button (the button below the "+" and "-" buttons). That will load the type names (e.g. cctrack). Now click on the `Choose preset` button (4th after the "+" - the one with the folder and heart) and choose a color preset. For this one I like "Traffic Lights". The colors are now set up.   

This configuration is in state file `outputpo_1.pvsm`. Below we will generate a screenshot with `pvpython` (you can load the state file and run it yourself in ParaView). 

In [45]:
!echo 'from paraview.simple import * ; \
       LoadState("state/popng_1.pvsm") ; \
       r = GetActiveViewOrCreate("RenderView") ; r.ViewSize=[800,600] ; \
       RenderAllViews() ; \
       SaveScreenshot("images/popng_1.png")' | pvpython

![Image](images/popng_1.png)

What you see is that the pmtracks and the costrks follow each other, except for one costrk (left side in picture above) that does not have a pmtrack counterpart. The cctracks are very short and rarely appear. 

Let's now put this in context by showing a picture of the detector and the tracks within. Load the `lariatBox.heprep.xml` file using the `View geometry` reader. Before hiting `Apply`, we want to configure the reader to only load certain structures. The wires in LAriat make up an enormous number of sctructures and are hard to visualize. So let's exclude the wires themselves by putting in the Regular Expression text box `TPCShieldPlane|TPCPlaneInduction|TPCPlaneCollection` and check the `Invert Regular Expression` box. You should get the same results as shown below (try the state file `outputpo_2.pvsm`).

Running `pvpython` below, we need the location of the `GeantToVTKPlugin`. Let's put that in a variable so you can easily change it to fit your installation.

In [32]:
geantToVtkPluginLocation = '/Users/lyon/ParaView/GeantToVTK-1.3/GeantToVTKPlugin.xml'

In [46]:
!echo 'from paraview.simple import * ; \
       LoadPlugin("{geantToVtkPluginLocation}", True, globals()); \
       LoadState("state/popng_2.pvsm") ; \
       r = GetActiveViewOrCreate("RenderView") ; r.ViewSize=[800,600] ; \
       RenderAllViews(); \
       SaveScreenshot("images/popng_2.png")' \
       | pvpython

![index](images/popng_2.png)

Let's try a movie. We will orbit about the detector. You can do this by creating a camera orbit centered on $(25,0,50)$ as that seems to be the center of the detector. Write out this state as `pomovie_1.pvsm`.


In [47]:
!echo 'from paraview.simple import * ; \
       LoadPlugin("{geantToVtkPluginLocation}", True, globals()); \
       LoadState("state/pomovie_1.pvsm") ; \
       r = GetActiveViewOrCreate("RenderView") ; r.ViewSize=[800,600] ; \
       RenderAllViews(); \
       WriteAnimation("movies/pomovie_1.ogv", Magnification=1, FrameRate=15.0, Compression=True)' \
       | pvpython

Note that we produced an `ogv` file. Most browsers can display them natively. We have to jump through some hoops though to load it. Let's make a function that we can reuse. 

In [37]:
from IPython.display import HTML
from base64 import b64encode
def makeMovie(filename):
    video = open(filename, "rb").read()
    video_encoded = b64encode(video).decode('ascii')
    video_tag = '<video controls alt="test" src="data:video/x-m4v;base64,{0}">'.format(video_encoded)
    return HTML(data=video_tag)

In [48]:
makeMovie("movies/pomovie_1.ogv")

In [49]:
tag = '<video controls><source src="movies/pomovie_1.ogv" type="video/ogg"></source></video>'
HTML(data=tag)

--- More to do here ---

## Track/hit movie

Make a movie showing the time evolution of a Lariat track. Jim Kowalkowski created some CSV files from Lariat data. 

The file `output_po.csv` has information on hits on tracks, including the $x,y,z$ position.

In [32]:
!head data20150919/output_po.csv

eid/I,type/S,id/I,index/I,x/F,y/F,z/F,dirx/F,diry/F,dirz/F,p/F
1,pmtrack,0,0,29.4108,-1.02638,50.6487,0.10971,0.035345,-0.993335,0
1,pmtrack,0,1,29.4585,-1.01102,50.217,0.10971,0.035345,-0.993335,0
1,pmtrack,0,2,29.5111,-0.994092,49.7413,0.10971,0.035345,-0.993335,0
1,pmtrack,0,3,29.541,-0.984435,49.4699,0.10971,0.035345,-0.993335,0
1,pmtrack,0,4,29.5606,-0.978127,49.2927,0.10971,0.035345,-0.993335,0
1,pmtrack,0,5,29.5959,-0.966758,48.9731,0.10971,0.035345,-0.993335,0
1,pmtrack,0,6,29.611,-0.961909,48.8369,0.10971,0.035345,-0.993335,0
1,pmtrack,0,7,29.6475,-0.95012,48.5055,0.10971,0.035345,-0.993335,0
1,pmtrack,0,8,29.6612,-0.945724,48.382,0.10971,0.035345,-0.993335,0


The file `output_ht.csv` has raw ADC and TDC information.

In [33]:
!head data20150919/output_ht.csv

eid/I,type/S,id/I,peaktime/F,chan/F,peakamp/F,sumadc/F,view/I,wire/S
1,pmtrack,0,1506.45,132,48.487,724.583,0,C:0 T:0 P:0 W:132
1,pmtrack,0,1501.37,131,19.7431,461.965,0,C:0 T:0 P:0 W:131
1,pmtrack,0,1512.35,130,8.46552,194.732,0,C:0 T:0 P:0 W:130
1,pmtrack,0,1508.53,369,13.2191,192.482,1,C:0 T:0 P:1 W:129
1,pmtrack,0,1513.47,129,8.85346,135.981,0,C:0 T:0 P:0 W:129
1,pmtrack,0,1519.69,368,11.4093,173.319,1,C:0 T:0 P:1 W:128
1,pmtrack,0,1517.19,128,8.6917,125.778,0,C:0 T:0 P:0 W:128
1,pmtrack,0,1521,367,10.6517,178.272,1,C:0 T:0 P:1 W:127
1,pmtrack,0,1520.57,127,7.12778,103.499,0,C:0 T:0 P:0 W:127


We need to merge the files so that we have $x,y,z$ and the hit information in one place.

Look at the lengths of the files

In [34]:
!wc data20150919/output_po.csv

     796     796   57087 data20150919/output_po.csv


In [35]:
!wc data20150919/output_ht.csv

     321    1281   19032 data20150919/output_ht.csv


There are many kinds of tracks in `output_po.csv`, but only one in `output_ht.csv` (pmtrack). Lets focus on those.

In [36]:
!grep pmtrack data20150919/output_po.csv | wc

     320     320   23127


This has one less than `output_ht.csv` due to the header in the latter. So it looks like the hits should line up.

Let's load them in with pandas and see if we can merge them.

In [37]:
import pandas as pd

In [38]:
pd.__version__

u'0.17.0rc1'

In [39]:
po = pd.read_csv("data20150919/output_po.csv")

In [40]:
po.head()

eid/I   type/S  id/I  index/I      x/F       y/F      z/F   dirx/F  \
0      1  pmtrack     0        0  29.4108 -1.026380  50.6487  0.10971   
1      1  pmtrack     0        1  29.4585 -1.011020  50.2170  0.10971   
2      1  pmtrack     0        2  29.5111 -0.994092  49.7413  0.10971   
3      1  pmtrack     0        3  29.5410 -0.984435  49.4699  0.10971   
4      1  pmtrack     0        4  29.5606 -0.978127  49.2927  0.10971   

     diry/F    dirz/F  p/F  
0  0.035345 -0.993335    0  
1  0.035345 -0.993335    0  
2  0.035345 -0.993335    0  
3  0.035345 -0.993335    0  
4  0.035345 -0.993335    0

In [41]:
ht = pd.read_csv("data20150919/output_ht.csv")

In [42]:
ht.head()

eid/I   type/S  id/I  peaktime/F  chan/F  peakamp/F  sumadc/F  view/I  \
0      1  pmtrack     0     1506.45     132   48.48700   724.583       0   
1      1  pmtrack     0     1501.37     131   19.74310   461.965       0   
2      1  pmtrack     0     1512.35     130    8.46552   194.732       0   
3      1  pmtrack     0     1508.53     369   13.21910   192.482       1   
4      1  pmtrack     0     1513.47     129    8.85346   135.981       0   

              wire/S  
0  C:0 T:0 P:0 W:132  
1  C:0 T:0 P:0 W:131  
2  C:0 T:0 P:0 W:130  
3  C:0 T:0 P:1 W:129  
4  C:0 T:0 P:0 W:129

In [43]:
len(ht), len(po)

(320, 795)

What are the kinds of tracks?

In [44]:
pd.unique( ht['type/S'] )

array(['pmtrack'], dtype=object)

In [45]:
pd.unique( po['type/S'])

array(['pmtrack', 'cctrack', 'costrk'], dtype=object)

So we only want the `pmtrack`.

In [46]:
popm = po[ po['type/S'] == 'pmtrack' ]

In [47]:
len(popm)

320

That matches `ht`

In [48]:
popm.head()

eid/I   type/S  id/I  index/I      x/F       y/F      z/F   dirx/F  \
0      1  pmtrack     0        0  29.4108 -1.026380  50.6487  0.10971   
1      1  pmtrack     0        1  29.4585 -1.011020  50.2170  0.10971   
2      1  pmtrack     0        2  29.5111 -0.994092  49.7413  0.10971   
3      1  pmtrack     0        3  29.5410 -0.984435  49.4699  0.10971   
4      1  pmtrack     0        4  29.5606 -0.978127  49.2927  0.10971   

     diry/F    dirz/F  p/F  
0  0.035345 -0.993335    0  
1  0.035345 -0.993335    0  
2  0.035345 -0.993335    0  
3  0.035345 -0.993335    0  
4  0.035345 -0.993335    0

Well, one final check can be how many hits there are per track (we'll count rows -- just need a column to do that with, so choose the event number - doesn't matter which column we choose)

In [49]:
ht[ ['id/I', 'eid/I'] ].groupby('id/I').count()

eid/I
id/I        
0        203
1         34
2         59
65539     24

In [50]:
popm[ ['id/I', 'eid/I'] ].groupby('id/I').count()

eid/I
id/I        
0        203
1         34
2         59
65539     24

They look the same! Let's merge them for conversion to VTK

We need to add an index to the ht hits. How to do this?

In [51]:
ht['index/I'] = ht.groupby(['id/I']).cumcount()

In [52]:
ht.head()

eid/I   type/S  id/I  peaktime/F  chan/F  peakamp/F  sumadc/F  view/I  \
0      1  pmtrack     0     1506.45     132   48.48700   724.583       0   
1      1  pmtrack     0     1501.37     131   19.74310   461.965       0   
2      1  pmtrack     0     1512.35     130    8.46552   194.732       0   
3      1  pmtrack     0     1508.53     369   13.21910   192.482       1   
4      1  pmtrack     0     1513.47     129    8.85346   135.981       0   

              wire/S  index/I  
0  C:0 T:0 P:0 W:132        0  
1  C:0 T:0 P:0 W:131        1  
2  C:0 T:0 P:0 W:130        2  
3  C:0 T:0 P:1 W:129        3  
4  C:0 T:0 P:0 W:129        4

The index columns should match in the two datasets

In [53]:
all(ht['index/I'] == popm['index/I'])

True

Let's merge!

In [54]:
htpm = pd.merge(ht, popm, on=['id/I', 'index/I'])

In [55]:
htpm.drop(['eid/I_x', 'eid/I_y', 'type/S_x', 'type/S_y'], axis=1, inplace=True)

In [56]:
htpm.head()

id/I  peaktime/F  chan/F  peakamp/F  sumadc/F  view/I             wire/S  \
0     0     1506.45     132   48.48700   724.583       0  C:0 T:0 P:0 W:132   
1     0     1501.37     131   19.74310   461.965       0  C:0 T:0 P:0 W:131   
2     0     1512.35     130    8.46552   194.732       0  C:0 T:0 P:0 W:130   
3     0     1508.53     369   13.21910   192.482       1  C:0 T:0 P:1 W:129   
4     0     1513.47     129    8.85346   135.981       0  C:0 T:0 P:0 W:129   

   index/I      x/F       y/F      z/F   dirx/F    diry/F    dirz/F  p/F  
0        0  29.4108 -1.026380  50.6487  0.10971  0.035345 -0.993335    0  
1        1  29.4585 -1.011020  50.2170  0.10971  0.035345 -0.993335    0  
2        2  29.5111 -0.994092  49.7413  0.10971  0.035345 -0.993335    0  
3        3  29.5410 -0.984435  49.4699  0.10971  0.035345 -0.993335    0  
4        4  29.5606 -0.978127  49.2927  0.10971  0.035345 -0.993335    0

In [57]:
len(htpm)

320

Write it out!

In [58]:
htpm.to_csv('output_htpm.csv', index=False)   # index=False says don't write the row name (it's empty)

In [59]:
!head output_htpm.csv

id/I,peaktime/F,chan/F,peakamp/F,sumadc/F,view/I,wire/S,index/I,x/F,y/F,z/F,dirx/F,diry/F,dirz/F,p/F
0,1506.45,132,48.487,724.583,0,C:0 T:0 P:0 W:132,0,29.4108,-1.02638,50.6487,0.10971,0.035345,-0.993335,0
0,1501.37,131,19.7431,461.965,0,C:0 T:0 P:0 W:131,1,29.4585,-1.01102,50.217,0.10971,0.035345,-0.993335,0
0,1512.35,130,8.46552,194.732,0,C:0 T:0 P:0 W:130,2,29.5111,-0.994092,49.7413,0.10971,0.035345,-0.993335,0
0,1508.53,369,13.2191,192.482,1,C:0 T:0 P:1 W:129,3,29.541,-0.984435,49.4699,0.10971,0.035345,-0.993335,0
0,1513.47,129,8.85346,135.981,0,C:0 T:0 P:0 W:129,4,29.5606,-0.978127,49.2927,0.10971,0.035345,-0.993335,0
0,1519.69,368,11.4093,173.319,1,C:0 T:0 P:1 W:128,5,29.5959,-0.966758,48.9731,0.10971,0.035345,-0.993335,0
0,1517.19,128,8.6917,125.778,0,C:0 T:0 P:0 W:128,6,29.611,-0.961909,48.8369,0.10971,0.035345,-0.993335,0
0,1521.0,367,10.6517,178.272,1,C:0 T:0 P:1 W:127,7,29.6475,-0.95012,48.5055,0.10971,0.035345,-0.993335,0
0,1520.57,127,7.12778,103.499,0,C:0 T:0 P:0 W:127,8,

Now convert to VTK

In [60]:
!pvpython convertCSV.py output_htpm.csv

Read File
[('id', '<i8'), ('peaktime', '<f8'), ('chan', '<f8'), ('peakamp', '<f8'), ('sumadc', '<f8'), ('view', '<i8'), ('wire', 'S20'), ('index', '<i8'), ('x', '<f8'), ('y', '<f8'), ('z', '<f8'), ('dirx', '<f8'), ('diry', '<f8'), ('dirz', '<f8'), ('p', '<f8')]
Assemble polydata
Making array id
Making array peaktime
Making array chan
Making array peakamp
Making array sumadc
Making array view
Making array (string) wire
Making array index
Making array dirx diry dirz
Making array p
Writing output_htpm.vtp


--- More to do here ---